In [13]:
import json, pickle
import numpy as np
from keras.models import Model
from keras.layers import Input, Embedding, Bidirectional, LSTM, TimeDistributed, Dense
from keras.preprocessing.sequence import pad_sequences
from keras.utils import to_categorical
from seqeval.metrics import classification_report
from sklearn.model_selection import train_test_split

In [14]:
#load the data
# with open("../dataset/dataset_ner_srl.json", encoding="utf-8") as f:
#     data = json.load(f)

# sentences = [[tok.lower() for tok in item["tokens"]] for item in data]
# labels_ner = [item["labels_ner"] for item in data]
# labels_srl = [item["labels_srl"] for item in data]

# for i, label_seq in enumerate(labels_ner):
#     if "V" in label_seq:
#         print(f"Label 'V' ditemukan di index {i}: {label_seq}")
        
        
data = []

with open("../dataset/dataset_ner_srl.tsv", encoding="utf-8") as f:
    tokens, ner_labels, srl_labels = [], [], []
    
    for line in f:
        line = line.strip()
        if not line:
            if tokens:
                data.append({
                    "tokens": tokens,
                    "labels_ner": ner_labels,
                    "labels_srl": srl_labels
                })
                tokens, ner_labels, srl_labels = [], [], []
        else:
            token, ner, srl = line.split("\t")
            tokens.append(token)
            ner_labels.append(ner)
            srl_labels.append(srl)

# Preprocessing sama seperti sebelumnya
sentences = [[tok.lower() for tok in item["tokens"]] for item in data]
labels_ner = [item["labels_ner"] for item in data]
labels_srl = [item["labels_srl"] for item in data]

total_kalimat = len(data)
total_token = sum(len(item["tokens"]) for item in data)

print("Total kalimat:", total_kalimat)
print("Total token:", total_token)

Total kalimat: 156
Total token: 1850


In [15]:
# tagging 
words = sorted({w for s in sentences for w in s})
ner_tags = sorted({t for seq in labels_ner for t in seq})
srl_tags = sorted({t for seq in labels_srl for t in seq})

word2idx = {w: i + 2 for i, w in enumerate(words)}
word2idx["PAD"], word2idx["UNK"] = 0, 1

tag2idx_ner = {t: i for i, t in enumerate(ner_tags)}
tag2idx_srl = {t: i for i, t in enumerate(srl_tags)}
idx2tag_ner = {i: t for t, i in tag2idx_ner.items()}
idx2tag_srl = {i: t for t, i in tag2idx_srl.items()}

In [16]:
# encoding

X = [[word2idx.get(w, word2idx["UNK"]) for w in s] for s in sentences]
y_ner = [[tag2idx_ner[t] for t in seq] for seq in labels_ner]
y_srl = [[tag2idx_srl[t] for t in seq] for seq in labels_srl]

maxlen = 50 

X = pad_sequences(X, maxlen=maxlen, padding="post", value=word2idx["PAD"])
y_ner = pad_sequences(y_ner, maxlen=maxlen, padding="post", value=tag2idx_ner["O"])
y_srl = pad_sequences(y_srl, maxlen=maxlen, padding="post", value=tag2idx_srl["O"])

y_ner = [to_categorical(seq, num_classes=len(tag2idx_ner)) for seq in y_ner]
y_srl = [to_categorical(seq, num_classes=len(tag2idx_srl)) for seq in y_srl]

X = np.array(X)
y_ner = np.array(y_ner)
y_srl = np.array(y_srl)

In [17]:
X_train, X_test, y_ner_train, y_ner_test, y_srl_train, y_srl_test = train_test_split(
    X, y_ner, y_srl,            
    test_size=0.20,             
    random_state=42,
    shuffle=True            
)

In [18]:
input_layer = Input(shape=(maxlen,))
embed = Embedding(len(word2idx), 64)(input_layer)
bilstm = Bidirectional(LSTM(64, return_sequences=True))(embed)

ner_output = TimeDistributed(
    Dense(len(tag2idx_ner), activation="softmax"), name="ner_output"
)(bilstm)
srl_output = TimeDistributed(
    Dense(len(tag2idx_srl), activation="softmax"), name="srl_output"
)(bilstm)

model = Model(inputs=input_layer, outputs=[ner_output, srl_output])
model.compile(
    optimizer="adam",
    loss={
        "ner_output": "categorical_crossentropy",
        "srl_output": "categorical_crossentropy",
    },
    metrics={"ner_output": "accuracy", "srl_output": "accuracy"},
)
model.summary()
model.fit(
    X_train, {"ner_output": y_ner_train, "srl_output": y_srl_train}, 
    validation_data=(X_test, {"ner_output": y_ner_test, "srl_output": y_srl_test}),
    batch_size=2,
    epochs=10,
    verbose=1
)

# ---------- 6. Simpan artefak ----------
model.save("multi_task_lstm_ner_srl_model.keras")
with open("word2idx.pkl", "wb") as f:
    pickle.dump(word2idx, f)
with open("tag2idx_ner.pkl", "wb") as f:
    pickle.dump(tag2idx_ner, f)
with open("tag2idx_srl.pkl", "wb") as f:
    pickle.dump(tag2idx_srl, f)


Model: "functional_1"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer_1       │ (None, 50)        │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding_1         │ (None, 50, 64)    │     44,544 │ input_layer_1[0]… │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ bidirectional_1     │ (None, 50, 128)   │     66,048 │ embedding_1[0][0] │
│ (Bidirectional)     │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ ner_output          │ (None, 50, 25)    │      3,225 │ bidirectional_1[… │
│ (TimeDistributed)   │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ srl_output          │ (None, 50, 18)    │      2,322 │ bidirectional_1[… │
│ (TimeDistributed)   │                   │            │                   │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 116,139 (453.67 KB)

 Trainable params: 116,139 (453.67 KB)

 Non-trainable params: 0 (0.00 B)

Epoch 1/10
62/62 ━━━━━━━━━━━━━━━━━━━━ 4s 19ms/step - loss: 3.2850 - ner_output_accuracy: 0.8700 - ner_output_loss: 1.6767 - srl_output_accuracy: 0.7518 - srl_output_loss: 1.6083 - val_loss: 0.7275 - val_ner_output_accuracy: 0.9519 - val_ner_output_loss: 0.2555 - val_srl_output_accuracy: 0.8450 - val_srl_output_loss: 0.4720
Epoch 2/10
62/62 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - loss: 0.7622 - ner_output_accuracy: 0.9528 - ner_output_loss: 0.2458 - srl_output_accuracy: 0.8296 - srl_output_loss: 0.5163 - val_loss: 0.6534 - val_ner_output_accuracy: 0.9519 - val_ner_output_loss: 0.2296 - val_srl_output_accuracy: 0.8531 - val_srl_output_loss: 0.4238
Epoch 3/10
62/62 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - loss: 0.6875 - ner_output_accuracy: 0.9572 - ner_output_loss: 0.2126 - srl_output_accuracy: 0.8496 - srl_output_loss: 0.4750 - val_loss: 0.6327 - val_ner_output_accuracy: 0.9519 - val_ner_output_loss: 0.2273 - val_srl_output_accuracy: 0.8688 - val_srl_output_loss: 0.4054
Epoch 4/10
62/62 ━━━━━━━━

In [19]:
# evaluation

results = model.evaluate(
    X_test,
    {"ner_output": y_ner_test, "srl_output": y_srl_test},
    verbose=0
)

# `metrics_names` = ["loss",
#                    "ner_output_loss", "srl_output_loss",
#                    "ner_output_accuracy", "srl_output_accuracy"]
print(dict(zip(model.metrics_names, results)))

def decode(pred, true, idx2tag):
    out_true, out_pred = [], []
    for p_seq, t_seq in zip(pred, true):
        t_labels, p_labels = [], []
        for p_tok, t_tok in zip(p_seq, t_seq):
            if t_tok.sum() == 0:          # token PAD → lewati
                continue
            t_labels.append(idx2tag[t_tok.argmax()])
            p_labels.append(idx2tag[p_tok.argmax()])
        out_true.append(t_labels)
        out_pred.append(p_labels)
    return out_true, out_pred

# prediksi hanya pada test set
y_pred_ner, y_pred_srl = model.predict(X_test, verbose=0)

true_ner, pred_ner = decode(y_pred_ner, y_ner_test, idx2tag_ner)
print(idx2tag_ner)
print("\n📊 [NER] Classification Report (test set):")
print(classification_report(true_ner, pred_ner, digits=2))




# y_pred_ner, y_pred_srl = model.predict(X, verbose=0)


# def decode(pred, true, idx2tag):
#     true_tags = [[idx2tag[np.argmax(tok)] for tok in seq] for seq in true]
#     pred_tags = [[idx2tag[np.argmax(tok)] for tok in seq] for seq in pred]
#     return true_tags, pred_tags


# true_ner, pred_ner = decode(y_pred_ner, y_ner, idx2tag_ner)

# print("\n📊 [NER] Classification Report:")
# print(classification_report(true_ner, pred_ner))



{'loss': 0.45865434408187866, 'compile_metrics': 0.159775510430336, 'ner_output_loss': 0.29887881875038147, 'srl_output_loss': 0.9550000429153442}
{0: 'B-DATE', 1: 'B-ETH', 2: 'B-EVENT', 3: 'B-LOC', 4: 'B-MIN', 5: 'B-MISC', 6: 'B-ORG', 7: 'B-PER', 8: 'B-QUANT', 9: 'B-REL', 10: 'B-RES', 11: 'B-TERM', 12: 'B-TIME', 13: 'I-DATE', 14: 'I-ETH', 15: 'I-EVENT', 16: 'I-LOC', 17: 'I-MISC', 18: 'I-ORG', 19: 'I-PER', 20: 'I-QUANT', 21: 'I-RES', 22: 'I-TERM', 23: 'I-TIME', 24: 'O'}

📊 [NER] Classification Report (test set):
              precision    recall  f1-score   support

        DATE       0.33      0.12      0.18         8
       EVENT       0.00      0.00      0.00         1
         LOC       1.00      0.04      0.07        28
         ORG       0.00      0.00      0.00         4
         PER       0.00      0.00      0.00         2
        TIME       0.50      0.30      0.37        10

   micro avg       0.50      0.09      0.16        53
   macro avg       0.31      0.08      0.10     

/mnt/disc1/code/thesis_quiz_project/lstm-quiz/myenv/lib64/python3.10/site-packages/seqeval/metrics/v1.py:57: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [20]:
# true_srl, pred_srl = decode(y_pred_srl, y_srl, idx2tag_srl)
# print("\n📊 [SRL] Classification Report:")
# print(classification_report(true_srl, pred_srl))

true_srl, pred_srl = decode(y_pred_srl, y_srl_test, idx2tag_srl)
print(idx2tag_srl)
print("\n📊 [SRL] Classification Report (test set):")
print(classification_report(true_srl, pred_srl, digits=2))

{0: 'ARG0', 1: 'ARG1', 2: 'ARG2', 3: 'ARG3', 4: 'ARGM-BNF', 5: 'ARGM-CAU', 6: 'ARGM-COM', 7: 'ARGM-FRQ', 8: 'ARGM-LOC', 9: 'ARGM-MNR', 10: 'ARGM-MOD', 11: 'ARGM-NEG', 12: 'ARGM-PRP', 13: 'ARGM-SRC', 14: 'ARGM-TMP', 15: 'O', 16: 'R-ARG1', 17: 'V'}

📊 [SRL] Classification Report (test set):
              precision    recall  f1-score   support

         CAU       0.00      0.00      0.00         1
         FRQ       0.00      0.00      0.00         1
         LOC       0.31      0.50      0.38        10
         MNR       0.00      0.00      0.00         4
         PRP       0.00      0.00      0.00         1
         RG0       0.50      0.11      0.17        19
         RG1       0.18      0.20      0.19        46
         RG2       0.27      0.40      0.32        10
         TMP       0.50      0.59      0.54        17
           _       0.12      0.03      0.05        33

   micro avg       0.28      0.22      0.24       142
   macro avg       0.19      0.18      0.17       142
weight

/mnt/disc1/code/thesis_quiz_project/lstm-quiz/myenv/lib64/python3.10/site-packages/seqeval/metrics/sequence_labeling.py:171: UserWarning: ARG1 seems not to be NE tag.
  warnings.warn('{} seems not to be NE tag.'.format(chunk))
/mnt/disc1/code/thesis_quiz_project/lstm-quiz/myenv/lib64/python3.10/site-packages/seqeval/metrics/sequence_labeling.py:171: UserWarning: V seems not to be NE tag.
  warnings.warn('{} seems not to be NE tag.'.format(chunk))
/mnt/disc1/code/thesis_quiz_project/lstm-quiz/myenv/lib64/python3.10/site-packages/seqeval/metrics/sequence_labeling.py:171: UserWarning: ARGM-TMP seems not to be NE tag.
  warnings.warn('{} seems not to be NE tag.'.format(chunk))
/mnt/disc1/code/thesis_quiz_project/lstm-quiz/myenv/lib64/python3.10/site-packages/seqeval/metrics/sequence_labeling.py:171: UserWarning: ARG0 seems not to be NE tag.
  warnings.warn('{} seems not to be NE tag.'.format(chunk))
/mnt/disc1/code/thesis_quiz_project/lstm-quiz/myenv/lib64/python3.10/site-packages/seqeval/